## FDTree Class

In [1]:
import numpy as np
import pickle
from scipy.sparse import find

class DecisionTreeModel:
    def __init__(self, source, depth_threshold=10, plambda=7, MSP_item=200):
        '''
            sMatrix: I*U matrix
            depth_threshold: terminate depth
            plambda: regularization parameter
            self.rI: dict { itemid1, itemid2, itemid3 ... }
            self.rU: dict {
                        userid1: { itemid11: rating11, itemid12: rating12, ... } rating of user 1
                        userid2: { itemid21: rating21, itemid22: rating22, ... } rating of user 2
                        userid3: ...
                     }
            self.lr_bound: dict {
                                level 0: [[left_bound, right_bound]], users' bound for one level, each ele in dictionary represents one node
                                level 1: [[left_bound, right_bound], [left_bound, right_bound], [left_bound, right_bound]], 3
                                level 2: ..., 9
                            } (bound means index)
            self.tree: []  all of userid
            self.split_item: list [
                    level 0: []
                    level 1: []
                    level 2: []
            ]
            self.sum_cur_t: dict {
                        itemid1: {'rating': sum of ratings for item 1, 'cnt': sum of users rated item 1}
                        itemid2: {'rating': sum of ratings for item 2, 'cnt': sum of users rated item 2}
                        ...
                    }
            self.sum_2_cur_t: dict {
                        itemid1: sum of square ratings for item 1
                        itemid2: sum of square ratings for item 2
                        ...
                    }
            self.biasU: dict {
                        userid1: bias1
                        userid2: bias2
                        ...
                    }
            every element represents ratings for one item, its order decide the users in tree nodes
        '''
        self.real_item_num = source.shape[0]
        x = find(source)
        itemset = x[0]
        userset = x[1]
        self.rU = {}
        self.global_mean = 0  # global average of ratings   
        self.depth_threshold = depth_threshold
        self.plambda = plambda
        self.cur_depth = 0
        self.MSP_item = MSP_item

        #### Calculate rate of progress ####
        self.node_num = 0
        self.cur_node = 0
        for i in range(self.depth_threshold):
            self.node_num += 3 ** i

        #### Generate rI, rU ####
        print("rU Generation start:")
        self.rI = list(set(source.nonzero()[0]))
        i = 0
        num_ratings = len(userset)
        for itemid, userid in zip(itemset, userset):
            if i % 10000 == 0:
                print("%.2f%%" % (100 * i / num_ratings))
            i += 1
            self.rU.setdefault(userid, {})[itemid] = source[itemid, userid]
            self.global_mean += source[itemid, userid]
        self.global_mean /= len(itemset)
        self.item_size = len(self.rI)
        self.user_size = len(self.rU)
        print("rU Generation DONE")

        #### Initiate Tree, lr_bound ####
        self.tree = list(self.rU.keys())
        self.split_item = []
        self.lr_bound = {'0': [[0, len(self.tree) - 1]]}

        #### Generate bias, sum_cur_t, sum_2_cur_t ####
        self.biasU = {}
        self.sum_cur_t = np.zeros(self.real_item_num)
        self.sum_2_cur_t = np.zeros(self.real_item_num)
        self.sum_cntt = np.zeros(self.real_item_num)
        print("bias, sum_cur_t, sum_2_cur_t Generation start:")
        i = 0
        for userid in self.rU:
            if i % 5000 == 0:
                print("%.2f%%" % (100 * i / (0.7 * 480189)))
            i += 1
            self.biasU[userid] = (sum(list(self.rU[userid].values())) \
                                     + self.plambda * self.global_mean) /   \
                                 (self.plambda + len(self.rU[userid]))
            user_all_rating_id = np.array(list(self.rU[userid].keys()))
            # print('user_all_rating_id ', user_all_rating_id[:])
            user_all_rating = np.array(list(self.rU[userid].values()))
            self.sum_cur_t[user_all_rating_id[:]] += user_all_rating[:] - self.biasU[userid]
            self.sum_2_cur_t[user_all_rating_id[:]] += (user_all_rating[:] - self.biasU[userid]) ** 2
            self.sum_cntt[user_all_rating_id[:]] += 1
        print("bias, sum_cur_t, sum_2_cur_t Generation DONE")

        print("Initiation DONE!")

    def calculate_error(self, sumt, sumt_2, cntt):
        ''' Calculate error for one item-split in one node '''
        Error_i = np.sum(sumt_2 - (sumt ** 2) / (cntt + 1e-9))

        return Error_i

    def generate_decision_tree(self, lr_bound_for_node, chosen_id):
        '''
            sumtL: dict {
                itemid1: {'rating': sum of ratings for item 1, 'cnt': sum of users rated item 1}
                itemid2: {'rating': sum of ratings for item 2, 'cnt': sum of users rated item 2}
                ...
            }
            sumtL_2: dict {
                itemid1: sum of square ratings for item 1
                itemid2: sum of square ratings for item 2
                ...
            }
            lr_bound_for_node: list [leftind, rightind] for one node
        '''

        #### Terminate ####
        self.cur_depth += 1
        if self.cur_depth > self.depth_threshold or len(chosen_id) == self.item_size:
            return

        #### Choose Most Popular Items of This Node ####
        num_rec = np.zeros(self.real_item_num)
        for userid in self.tree[lr_bound_for_node[0]:(lr_bound_for_node[1] + 1)]:
            user_all_rating_id = np.array(list(self.rU[userid].keys()))
            num_rec[user_all_rating_id[:]] += 1
        sub_item_id = np.argsort(num_rec)[:self.MSP_item]

        #### Find optimum item to split ####
        min_sumtL, min_sumtD, min_sumtL_2, min_sumtD_2, min_sumtU, min_sumtU_2, Error = {}, {}, {}, {}, {}, {}, {}
        min_Error = "None"
        for itemid in sub_item_id:
            if itemid in chosen_id:
                continue
            '''
                user_rating_item_in_nodet: [ [uid01, rating01], [uid02, rating02], ... ]
                to find all users in node t who rates item i
            '''
            user_rating_item_in_nodet = ([userid, self.rU[userid][itemid]] for userid in
                                         self.tree[lr_bound_for_node[0]:(lr_bound_for_node[1] + 1)] if
                                         itemid in self.rU[userid])
            sumt = np.zeros((self.real_item_num, 3))
            sumt_2 = np.zeros((self.real_item_num, 3))
            cntt = np.zeros((self.real_item_num, 3))
            for user in user_rating_item_in_nodet:
                ''' user_all_rating: array [ [itemid11, rating11], [itemid12, rating12], ... ] '''
                user_all_rating_id = np.array(list(self.rU[user[0]].keys()))
                user_all_rating = np.array(list(self.rU[user[0]].values()))
                #### calculate sumtL for node LIKE ####
                if user[1] >= 4:
                    sumt[user_all_rating_id[:], 0] += user_all_rating[:] - self.biasU[user[0]]
                    sumt_2[user_all_rating_id[:], 0] += (user_all_rating[:] - self.biasU[user[0]]) ** 2
                    cntt[user_all_rating_id[:], 0] += 1
                #### calculate sumtD for node DISLIKE ####
                elif user[1] <= 3:
                    sumt[user_all_rating_id[:], 1] += user_all_rating[:] - self.biasU[user[0]]
                    sumt_2[user_all_rating_id[:], 1] += (user_all_rating[:] - self.biasU[user[0]]) ** 2
                    cntt[user_all_rating_id[:], 1] += 1
            #### calculate sumtU for node UNKNOWN ####
            sumt[:, 2] = self.sum_cur_t[:] - sumt[:, 0] - sumt[:, 1]
            sumt_2[:, 2] = self.sum_2_cur_t[:] - sumt_2[:, 0] - sumt_2[:, 1]
            cntt[:, 2] = self.sum_cntt[:] - cntt[:, 0] - cntt[:, 1]
            Error[itemid] = self.calculate_error(sumt, sumt_2, cntt)

            if min_Error == "None" or Error[itemid] < min_Error:
                min_sumt = sumt
                min_sumt_2 = sumt_2
                min_cntt = cntt
                min_Error = Error[itemid]
        #### Find optimum split-item ####
        optimum_itemid = min(Error, key=Error.get)
        if len(self.split_item) == self.cur_depth - 1:
            self.split_item.append([optimum_itemid])
        else:
            self.split_item[self.cur_depth - 1].append(optimum_itemid)
        # self.split_item.setdefault(str(self.cur_depth-1), []).append(optimum_itemid)
        chosen_id.append(optimum_itemid)

        #### sort tree ####
        self.lr_bound.setdefault(str(self.cur_depth), []).append([])  # for LIKE
        self.lr_bound[str(self.cur_depth)].append([])  # for DISLIKE
        self.lr_bound[str(self.cur_depth)].append([])  # for UNKNOWN
        listU, listL, listD = [], [], []
        for userid in self.tree[lr_bound_for_node[0]:(lr_bound_for_node[1] + 1)]:
            if optimum_itemid not in self.rU[userid]:
                listU.append(userid)
            elif self.rU[userid][optimum_itemid] >= 4:
                listL.append(userid)
            elif self.rU[userid][optimum_itemid] <= 3:
                listD.append(userid)
        self.tree[lr_bound_for_node[0]:(lr_bound_for_node[1] + 1)] = listL + listD + listU
        self.lr_bound[str(self.cur_depth)][-3] = [lr_bound_for_node[0],
                                                  lr_bound_for_node[0] + len(listL) - 1]  # for LIKE
        self.lr_bound[str(self.cur_depth)][-2] = [lr_bound_for_node[0] + len(listL),
                                                  lr_bound_for_node[0] + len(listL) + len(listD) - 1]  # for DISLIKE
        self.lr_bound[str(self.cur_depth)][-1] = [lr_bound_for_node[0] + len(listL) + len(listD),
                                                  lr_bound_for_node[0] + len(listL) + len(listD) + len(
                                                      listU) - 1]  # for UNKNOWN

        #### Generate Subtree of Node LIKE ####
        self.sum_cur_t = min_sumt[:, 0]
        self.sum_2_cur_t = min_sumt_2[:, 0]
        self.sum_cntt = min_cntt[:, 0]
        self.generate_decision_tree(self.lr_bound[str(self.cur_depth)][-3], chosen_id[:])
        self.cur_depth -= 1

        #### Generate Subtree of Node DISLIKE ####
        self.sum_cur_t = min_sumt[:, 1]
        self.sum_2_cur_t = min_sumt_2[:, 1]
        self.sum_cntt = min_cntt[:, 1]
        self.generate_decision_tree(self.lr_bound[str(self.cur_depth)][-2], chosen_id[:])
        self.cur_depth -= 1

        #### Generate Subtree of Node UNKNOWN ####
        self.sum_cur_t = min_sumt[:, 2]
        self.sum_2_cur_t = min_sumt_2[:, 2]
        self.sum_cntt = min_cntt[:, 2]
        self.generate_decision_tree(self.lr_bound[str(self.cur_depth)][-1], chosen_id[:])
        self.cur_depth -= 1

        #### Show Rating Progress ####
        for i in range(self.cur_depth - 1):
            print("┃", end="")
        print("┏", end="")
        self.cur_node += 1
        print("Current depth: " + str(self.cur_depth) + "        %.2f%%" % (100 * self.cur_node / self.node_num))

    def build_model(self):
        #### Construct the tree & get the prediction model ####
        self.generate_decision_tree(self.lr_bound['0'][0], [])

## Step 1: Input Dataset

In [6]:
from scipy.sparse import load_npz

In [7]:
############### Load Data ##################
rating_matrix_csc = load_npz('netflix/sparse_matrix_100%.npz').tocsc()
print("file load DONE")
############################################

file load DONE


In [4]:
''' Save to file 'tree.pkl' '''
start = 0
end = int(rating_matrix_csc.shape[1] * 0.75)

In [5]:
dtmodel_realdata = DecisionTreeModel(rating_matrix_csc[:, start:end], depth_threshold = 10)

rU Generation start:
0.00%
0.01%
0.03%
0.04%
0.05%
0.07%
0.08%
0.09%
0.11%
0.12%
0.13%
0.15%
0.16%
0.17%
0.19%
0.20%
0.22%
0.23%
0.24%
0.26%
0.27%
0.28%
0.30%
0.31%
0.32%
0.34%
0.35%
0.36%
0.38%
0.39%
0.40%
0.42%
0.43%
0.44%
0.46%
0.47%
0.48%
0.50%
0.51%
0.52%
0.54%
0.55%
0.57%
0.58%
0.59%
0.61%
0.62%
0.63%
0.65%
0.66%
0.67%
0.69%
0.70%
0.71%
0.73%
0.74%
0.75%
0.77%
0.78%
0.79%
0.81%
0.82%
0.83%
0.85%
0.86%
0.87%
0.89%
0.90%
0.92%
0.93%
0.94%
0.96%
0.97%
0.98%
1.00%
1.01%
1.02%
1.04%
1.05%
1.06%
1.08%
1.09%
1.10%
1.12%
1.13%
1.14%
1.16%
1.17%
1.18%
1.20%
1.21%
1.22%
1.24%
1.25%
1.27%
1.28%
1.29%
1.31%
1.32%
1.33%
1.35%
1.36%
1.37%
1.39%
1.40%
1.41%
1.43%
1.44%
1.45%
1.47%
1.48%
1.49%
1.51%
1.52%
1.53%
1.55%
1.56%
1.57%
1.59%
1.60%
1.61%
1.63%
1.64%
1.66%
1.67%
1.68%
1.70%
1.71%
1.72%
1.74%
1.75%
1.76%
1.78%
1.79%
1.80%
1.82%
1.83%
1.84%
1.86%
1.87%
1.88%
1.90%
1.91%
1.92%
1.94%
1.95%
1.96%
1.98%
1.99%
2.01%
2.02%
2.03%
2.05%
2.06%
2.07%
2.09%
2.10%
2.11%
2.13%
2.14%
2.15%
2.17%
2.18%
2

17.15%
17.16%
17.17%
17.19%
17.20%
17.21%
17.23%
17.24%
17.25%
17.27%
17.28%
17.29%
17.31%
17.32%
17.33%
17.35%
17.36%
17.37%
17.39%
17.40%
17.41%
17.43%
17.44%
17.45%
17.47%
17.48%
17.50%
17.51%
17.52%
17.54%
17.55%
17.56%
17.58%
17.59%
17.60%
17.62%
17.63%
17.64%
17.66%
17.67%
17.68%
17.70%
17.71%
17.72%
17.74%
17.75%
17.76%
17.78%
17.79%
17.80%
17.82%
17.83%
17.84%
17.86%
17.87%
17.89%
17.90%
17.91%
17.93%
17.94%
17.95%
17.97%
17.98%
17.99%
18.01%
18.02%
18.03%
18.05%
18.06%
18.07%
18.09%
18.10%
18.11%
18.13%
18.14%
18.15%
18.17%
18.18%
18.19%
18.21%
18.22%
18.24%
18.25%
18.26%
18.28%
18.29%
18.30%
18.32%
18.33%
18.34%
18.36%
18.37%
18.38%
18.40%
18.41%
18.42%
18.44%
18.45%
18.46%
18.48%
18.49%
18.50%
18.52%
18.53%
18.54%
18.56%
18.57%
18.59%
18.60%
18.61%
18.63%
18.64%
18.65%
18.67%
18.68%
18.69%
18.71%
18.72%
18.73%
18.75%
18.76%
18.77%
18.79%
18.80%
18.81%
18.83%
18.84%
18.85%
18.87%
18.88%
18.89%
18.91%
18.92%
18.93%
18.95%
18.96%
18.98%
18.99%
19.00%
19.02%
19.03%
19.04%
19.06%

32.90%
32.92%
32.93%
32.94%
32.96%
32.97%
32.98%
33.00%
33.01%
33.03%
33.04%
33.05%
33.07%
33.08%
33.09%
33.11%
33.12%
33.13%
33.15%
33.16%
33.17%
33.19%
33.20%
33.21%
33.23%
33.24%
33.25%
33.27%
33.28%
33.29%
33.31%
33.32%
33.33%
33.35%
33.36%
33.38%
33.39%
33.40%
33.42%
33.43%
33.44%
33.46%
33.47%
33.48%
33.50%
33.51%
33.52%
33.54%
33.55%
33.56%
33.58%
33.59%
33.60%
33.62%
33.63%
33.64%
33.66%
33.67%
33.68%
33.70%
33.71%
33.73%
33.74%
33.75%
33.77%
33.78%
33.79%
33.81%
33.82%
33.83%
33.85%
33.86%
33.87%
33.89%
33.90%
33.91%
33.93%
33.94%
33.95%
33.97%
33.98%
33.99%
34.01%
34.02%
34.03%
34.05%
34.06%
34.07%
34.09%
34.10%
34.12%
34.13%
34.14%
34.16%
34.17%
34.18%
34.20%
34.21%
34.22%
34.24%
34.25%
34.26%
34.28%
34.29%
34.30%
34.32%
34.33%
34.34%
34.36%
34.37%
34.38%
34.40%
34.41%
34.42%
34.44%
34.45%
34.47%
34.48%
34.49%
34.51%
34.52%
34.53%
34.55%
34.56%
34.57%
34.59%
34.60%
34.61%
34.63%
34.64%
34.65%
34.67%
34.68%
34.69%
34.71%
34.72%
34.73%
34.75%
34.76%
34.77%
34.79%
34.80%
34.82%

48.66%
48.68%
48.69%
48.70%
48.72%
48.73%
48.74%
48.76%
48.77%
48.78%
48.80%
48.81%
48.82%
48.84%
48.85%
48.86%
48.88%
48.89%
48.91%
48.92%
48.93%
48.95%
48.96%
48.97%
48.99%
49.00%
49.01%
49.03%
49.04%
49.05%
49.07%
49.08%
49.09%
49.11%
49.12%
49.13%
49.15%
49.16%
49.17%
49.19%
49.20%
49.21%
49.23%
49.24%
49.26%
49.27%
49.28%
49.30%
49.31%
49.32%
49.34%
49.35%
49.36%
49.38%
49.39%
49.40%
49.42%
49.43%
49.44%
49.46%
49.47%
49.48%
49.50%
49.51%
49.52%
49.54%
49.55%
49.56%
49.58%
49.59%
49.61%
49.62%
49.63%
49.65%
49.66%
49.67%
49.69%
49.70%
49.71%
49.73%
49.74%
49.75%
49.77%
49.78%
49.79%
49.81%
49.82%
49.83%
49.85%
49.86%
49.87%
49.89%
49.90%
49.91%
49.93%
49.94%
49.96%
49.97%
49.98%
50.00%
50.01%
50.02%
50.04%
50.05%
50.06%
50.08%
50.09%
50.10%
50.12%
50.13%
50.14%
50.16%
50.17%
50.18%
50.20%
50.21%
50.22%
50.24%
50.25%
50.26%
50.28%
50.29%
50.30%
50.32%
50.33%
50.35%
50.36%
50.37%
50.39%
50.40%
50.41%
50.43%
50.44%
50.45%
50.47%
50.48%
50.49%
50.51%
50.52%
50.53%
50.55%
50.56%
50.57%

64.42%
64.44%
64.45%
64.46%
64.48%
64.49%
64.50%
64.52%
64.53%
64.54%
64.56%
64.57%
64.58%
64.60%
64.61%
64.62%
64.64%
64.65%
64.66%
64.68%
64.69%
64.70%
64.72%
64.73%
64.75%
64.76%
64.77%
64.79%
64.80%
64.81%
64.83%
64.84%
64.85%
64.87%
64.88%
64.89%
64.91%
64.92%
64.93%
64.95%
64.96%
64.97%
64.99%
65.00%
65.01%
65.03%
65.04%
65.05%
65.07%
65.08%
65.09%
65.11%
65.12%
65.14%
65.15%
65.16%
65.18%
65.19%
65.20%
65.22%
65.23%
65.24%
65.26%
65.27%
65.28%
65.30%
65.31%
65.32%
65.34%
65.35%
65.36%
65.38%
65.39%
65.40%
65.42%
65.43%
65.44%
65.46%
65.47%
65.49%
65.50%
65.51%
65.53%
65.54%
65.55%
65.57%
65.58%
65.59%
65.61%
65.62%
65.63%
65.65%
65.66%
65.67%
65.69%
65.70%
65.71%
65.73%
65.74%
65.75%
65.77%
65.78%
65.79%
65.81%
65.82%
65.84%
65.85%
65.86%
65.88%
65.89%
65.90%
65.92%
65.93%
65.94%
65.96%
65.97%
65.98%
66.00%
66.01%
66.02%
66.04%
66.05%
66.06%
66.08%
66.09%
66.10%
66.12%
66.13%
66.14%
66.16%
66.17%
66.18%
66.20%
66.21%
66.23%
66.24%
66.25%
66.27%
66.28%
66.29%
66.31%
66.32%
66.33%

80.18%
80.19%
80.21%
80.22%
80.23%
80.25%
80.26%
80.28%
80.29%
80.30%
80.32%
80.33%
80.34%
80.36%
80.37%
80.38%
80.40%
80.41%
80.42%
80.44%
80.45%
80.46%
80.48%
80.49%
80.50%
80.52%
80.53%
80.54%
80.56%
80.57%
80.58%
80.60%
80.61%
80.63%
80.64%
80.65%
80.67%
80.68%
80.69%
80.71%
80.72%
80.73%
80.75%
80.76%
80.77%
80.79%
80.80%
80.81%
80.83%
80.84%
80.85%
80.87%
80.88%
80.89%
80.91%
80.92%
80.93%
80.95%
80.96%
80.98%
80.99%
81.00%
81.02%
81.03%
81.04%
81.06%
81.07%
81.08%
81.10%
81.11%
81.12%
81.14%
81.15%
81.16%
81.18%
81.19%
81.20%
81.22%
81.23%
81.24%
81.26%
81.27%
81.28%
81.30%
81.31%
81.32%
81.34%
81.35%
81.37%
81.38%
81.39%
81.41%
81.42%
81.43%
81.45%
81.46%
81.47%
81.49%
81.50%
81.51%
81.53%
81.54%
81.55%
81.57%
81.58%
81.59%
81.61%
81.62%
81.63%
81.65%
81.66%
81.67%
81.69%
81.70%
81.72%
81.73%
81.74%
81.76%
81.77%
81.78%
81.80%
81.81%
81.82%
81.84%
81.85%
81.86%
81.88%
81.89%
81.90%
81.92%
81.93%
81.94%
81.96%
81.97%
81.98%
82.00%
82.01%
82.02%
82.04%
82.05%
82.07%
82.08%
82.09%

95.94%
95.95%
95.97%
95.98%
95.99%
96.01%
96.02%
96.03%
96.05%
96.06%
96.07%
96.09%
96.10%
96.11%
96.13%
96.14%
96.16%
96.17%
96.18%
96.20%
96.21%
96.22%
96.24%
96.25%
96.26%
96.28%
96.29%
96.30%
96.32%
96.33%
96.34%
96.36%
96.37%
96.38%
96.40%
96.41%
96.42%
96.44%
96.45%
96.46%
96.48%
96.49%
96.51%
96.52%
96.53%
96.55%
96.56%
96.57%
96.59%
96.60%
96.61%
96.63%
96.64%
96.65%
96.67%
96.68%
96.69%
96.71%
96.72%
96.73%
96.75%
96.76%
96.77%
96.79%
96.80%
96.81%
96.83%
96.84%
96.86%
96.87%
96.88%
96.90%
96.91%
96.92%
96.94%
96.95%
96.96%
96.98%
96.99%
97.00%
97.02%
97.03%
97.04%
97.06%
97.07%
97.08%
97.10%
97.11%
97.12%
97.14%
97.15%
97.16%
97.18%
97.19%
97.21%
97.22%
97.23%
97.25%
97.26%
97.27%
97.29%
97.30%
97.31%
97.33%
97.34%
97.35%
97.37%
97.38%
97.39%
97.41%
97.42%
97.43%
97.45%
97.46%
97.47%
97.49%
97.50%
97.51%
97.53%
97.54%
97.55%
97.57%
97.58%
97.60%
97.61%
97.62%
97.64%
97.65%
97.66%
97.68%
97.69%
97.70%
97.72%
97.73%
97.74%
97.76%
97.77%
97.78%
97.80%
97.81%
97.82%
97.84%
97.85%

In [6]:
dtmodel_realdata.build_model()

┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.00%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.01%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.01%
┃┃┃┃┃┃┃┃┏Current depth: 9        0.01%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.02%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.02%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.02%
┃┃┃┃┃┃┃┃┏Current depth: 9        0.03%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.03%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.03%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.04%
┃┃┃┃┃┃┃┃┏Current depth: 9        0.04%
┃┃┃┃┃┃┃┏Current depth: 8        0.04%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.05%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.05%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.05%
┃┃┃┃┃┃┃┃┏Current depth: 9        0.06%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.06%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.06%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.07%
┃┃┃┃┃┃┃┃┏Current depth: 9        0.07%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.07%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.08%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.08%
┃┃┃┃┃┃┃┃┏Current depth: 9    

┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.70%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.70%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.70%
┃┃┃┃┃┃┃┃┏Current depth: 9        0.71%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.71%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.71%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.72%
┃┃┃┃┃┃┃┃┏Current depth: 9        0.72%
┃┃┃┃┃┃┃┏Current depth: 8        0.72%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.73%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.73%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.73%
┃┃┃┃┃┃┃┃┏Current depth: 9        0.74%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.74%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.75%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.75%
┃┃┃┃┃┃┃┃┏Current depth: 9        0.75%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.76%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.76%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.76%
┃┃┃┃┃┃┃┃┏Current depth: 9        0.77%
┃┃┃┃┃┃┃┏Current depth: 8        0.77%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.77%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.78%
┃┃┃┃┃┃┃┃┃┏Current depth: 10     

┃┃┃┃┃┃┃┃┃┏Current depth: 10        1.39%
┃┃┃┃┃┃┃┃┏Current depth: 9        1.40%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        1.40%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        1.40%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        1.41%
┃┃┃┃┃┃┃┃┏Current depth: 9        1.41%
┃┃┃┃┃┃┃┏Current depth: 8        1.41%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        1.42%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        1.42%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        1.42%
┃┃┃┃┃┃┃┃┏Current depth: 9        1.43%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        1.43%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        1.43%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        1.44%
┃┃┃┃┃┃┃┃┏Current depth: 9        1.44%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        1.44%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        1.45%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        1.45%
┃┃┃┃┃┃┃┃┏Current depth: 9        1.45%
┃┃┃┃┃┃┃┏Current depth: 8        1.46%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        1.46%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        1.46%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        1.47%
┃┃┃┃┃┃┃┃┏Current depth: 9        1.47%
┃┃┃┃┃┃┃┃┃┏Current depth: 10       

┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.08%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.09%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.09%
┃┃┃┃┃┃┃┃┏Current depth: 9        2.09%
┃┃┃┃┃┃┃┏Current depth: 8        2.10%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.10%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.10%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.11%
┃┃┃┃┃┃┃┃┏Current depth: 9        2.11%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.11%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.12%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.12%
┃┃┃┃┃┃┃┃┏Current depth: 9        2.12%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.13%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.13%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.13%
┃┃┃┃┃┃┃┃┏Current depth: 9        2.14%
┃┃┃┃┃┃┃┏Current depth: 8        2.14%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.14%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.15%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.15%
┃┃┃┃┃┃┃┃┏Current depth: 9        2.15%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.16%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.16%
┃┃┃┃┃┃┃┃┃┏Current depth: 10     

┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.77%
┃┃┃┃┃┃┃┃┏Current depth: 9        2.78%
┃┃┃┃┃┃┃┏Current depth: 8        2.78%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.78%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.79%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.79%
┃┃┃┃┃┃┃┃┏Current depth: 9        2.79%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.80%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.80%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.80%
┃┃┃┃┃┃┃┃┏Current depth: 9        2.81%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.81%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.81%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.82%
┃┃┃┃┃┃┃┃┏Current depth: 9        2.82%
┃┃┃┃┃┃┃┏Current depth: 8        2.82%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.83%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.83%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.83%
┃┃┃┃┃┃┃┃┏Current depth: 9        2.84%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.84%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.85%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.85%
┃┃┃┃┃┃┃┃┏Current depth: 9        2.85%
┃┃┃┃┃┃┃┃┃┏Current depth: 10       

...

┃┃┃┃┃┃┃┃┃┏Current depth: 10        96.63%
┃┃┃┃┃┃┃┃┏Current depth: 9        96.63%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        96.63%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        96.64%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        96.64%
┃┃┃┃┃┃┃┃┏Current depth: 9        96.64%
┃┃┃┃┃┃┃┏Current depth: 8        96.65%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        96.65%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        96.65%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        96.66%
┃┃┃┃┃┃┃┃┏Current depth: 9        96.66%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        96.66%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        96.67%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        96.67%
┃┃┃┃┃┃┃┃┏Current depth: 9        96.67%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        96.68%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        96.68%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        96.68%
┃┃┃┃┃┃┃┃┏Current depth: 9        96.69%
┃┃┃┃┃┃┃┏Current depth: 8        96.69%
┃┃┃┃┃┃┏Current depth: 7        96.69%
┃┃┃┃┃┏Current depth: 6        96.70%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        96.70%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        96.70%
┃┃┃┃┃┃┃┃┃┏Current

┃┃┃┃┃┃┃┃┃┏Current depth: 10        97.30%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        97.31%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        97.31%
┃┃┃┃┃┃┃┃┏Current depth: 9        97.31%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        97.32%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        97.32%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        97.32%
┃┃┃┃┃┃┃┃┏Current depth: 9        97.33%
┃┃┃┃┃┃┃┏Current depth: 8        97.33%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        97.33%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        97.34%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        97.34%
┃┃┃┃┃┃┃┃┏Current depth: 9        97.34%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        97.35%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        97.35%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        97.35%
┃┃┃┃┃┃┃┃┏Current depth: 9        97.36%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        97.36%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        97.36%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        97.37%
┃┃┃┃┃┃┃┃┏Current depth: 9        97.37%
┃┃┃┃┃┃┃┏Current depth: 8        97.38%
┃┃┃┃┃┃┏Current depth: 7        97.38%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        97.38%
┃┃┃┃┃┃┃┃┃┏Cu

┃┃┃┃┃┃┃┃┃┏Current depth: 10        97.98%
┃┃┃┃┃┃┃┃┏Current depth: 9        97.99%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        97.99%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        97.99%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        98.00%
┃┃┃┃┃┃┃┃┏Current depth: 9        98.00%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        98.01%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        98.01%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        98.01%
┃┃┃┃┃┃┃┃┏Current depth: 9        98.02%
┃┃┃┃┃┃┃┏Current depth: 8        98.02%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        98.02%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        98.03%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        98.03%
┃┃┃┃┃┃┃┃┏Current depth: 9        98.03%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        98.04%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        98.04%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        98.04%
┃┃┃┃┃┃┃┃┏Current depth: 9        98.05%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        98.05%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        98.05%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        98.06%
┃┃┃┃┃┃┃┃┏Current depth: 9        98.06%
┃┃┃┃┃┃┃┏Current depth: 8        98.06%
┃┃┃┃┃┃┏Cur

┃┃┃┃┃┃┃┃┃┏Current depth: 10        98.66%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        98.66%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        98.67%
┃┃┃┃┃┃┃┃┏Current depth: 9        98.67%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        98.67%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        98.68%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        98.68%
┃┃┃┃┃┃┃┃┏Current depth: 9        98.68%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        98.69%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        98.69%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        98.69%
┃┃┃┃┃┃┃┃┏Current depth: 9        98.70%
┃┃┃┃┃┃┃┏Current depth: 8        98.70%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        98.70%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        98.71%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        98.71%
┃┃┃┃┃┃┃┃┏Current depth: 9        98.71%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        98.72%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        98.72%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        98.72%
┃┃┃┃┃┃┃┃┏Current depth: 9        98.73%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        98.73%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        98.73%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        98.74%
┃┃┃┃┃

┃┃┃┃┃┃┃┃┃┏Current depth: 10        99.34%
┃┃┃┃┃┃┃┃┏Current depth: 9        99.34%
┃┃┃┃┃┃┃┏Current depth: 8        99.34%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        99.35%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        99.35%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        99.35%
┃┃┃┃┃┃┃┃┏Current depth: 9        99.36%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        99.36%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        99.36%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        99.37%
┃┃┃┃┃┃┃┃┏Current depth: 9        99.37%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        99.37%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        99.38%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        99.38%
┃┃┃┃┃┃┃┃┏Current depth: 9        99.38%
┃┃┃┃┃┃┃┏Current depth: 8        99.39%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        99.39%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        99.39%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        99.40%
┃┃┃┃┃┃┃┃┏Current depth: 9        99.40%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        99.40%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        99.41%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        99.41%
┃┃┃┃┃┃┃┃┏Current depth: 9        99.41%
┃┃┃┃┃┃┃┃┃┏

In [10]:
del dtmodel_realdata.biasU
del dtmodel_realdata.sum_cur_t
del dtmodel_realdata.sum_2_cur_t
del dtmodel_realdata.sum_cntt

In [14]:
del rating_matrix_csc

In [23]:
import sys
sys.getsizeof(dtmodel_realdata.tree)+\
sys.getsizeof(dtmodel_realdata.split_item)+\
sys.getsizeof(dtmodel_realdata.lr_bound) 

3242216

In [8]:
import klepto
d = klepto.archives.dir_archive('tree', cached=True, serialized=True)
import numpy
# add three entries to the memory cache
d['matrix'] = rating_matrix_csc
# dump from memory cache to the on-disk archive
d.dump()
# clear the memory cache
d.clear()
d

dir_archive('tree', {}, cached=True)

In [4]:
import klepto
d = klepto.archives.dir_archive('tree', cached=True, serialized=True)
d.load('tree')

KeyError: 'K_I_7e61580abae749bfffdfb1366e788de7'

## remaining part

In [ ]:
######################## Build Predict Model #########################
plambda_candidates = {}
inputf = open('./tree_data_structure/tree.pkl', 'rb')
dtmodel_realdata = pickle.load(inputf)
for level in dtmodel_realdata.lr_bound:
	plambda_candidates[level] = list(np.arange(0.001, 0.05, 0.0005))
prediction_model = tf.generate_prediction_model(dtmodel_realdata, plambda_candidates, rating_matrix_csc[:, endt:end])
######################################################################

######################### Test for New-user ##########################
rmse_result = tf.pred_RMSE_for_new_user(dtmodel_realdata, prediction_model, rating_matrix_csc[:, end:])
######################################################################

## test with small dataset

In [9]:
import pandas as pd
from scipy.sparse import *
catagory = "Grocery_and_Gourmet_Food"
item_data = 'item_metadata/meta_' + catagory + '.csv'
rating_data = 'user_ratings/' + catagory + '.csv'
# print(rating_data)
ratingsFrame = pd.read_csv(rating_data, names = ["userID", "itemID", "rating"])
ratingsFrame.sort_values(by = 'userID', ascending=True, inplace=True)
itemsFrame = pd.read_csv(item_data)
item_lst = ratingsFrame["itemID"].tolist()
user_lst = ratingsFrame["userID"].tolist()
rating_lst = ratingsFrame["rating"].tolist()
row = []
col = []
rating_data = []
for i in range(ratingsFrame.shape[0]):
    row.append(item_lst[i])
    col.append(user_lst[i])
    rating_data.append(rating_lst[i])
print(user_lst[len(user_lst)-1])
rating_martix_coo = coo_matrix((rating_data, (row, col)), shape=(itemsFrame.shape[0], user_lst[len(user_lst)-1]+1))
rating_martix_csc = rating_martix_coo.tocsc()
rating_martix_csr = rating_martix_coo.tocsr()
start = 0
end = int(rating_martix_csc.shape[1] * 0.7)
sM_training = rating_martix_csc[:, start:end]
sM_testing =  rating_martix_csc[:, end:]

1748


In [11]:
############### Build Tree #################
''' Save to file 'tree.pkl' '''
dtmodel_realdata = DecisionTreeModel(sM_training, depth_threshold = 10)
dtmodel_realdata.build_model()
############################################

rU Generation start:
0.00%
37.99%
75.98%
rU Generation DONE
bias, sum_cur_t, sum_2_cur_t Generation start:
0.00%
bias, sum_cur_t, sum_2_cur_t Generation DONE
Initiation DONE!
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.00%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.01%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.01%
┃┃┃┃┃┃┃┃┏Current depth: 9        0.01%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.02%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.02%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.02%
┃┃┃┃┃┃┃┃┏Current depth: 9        0.03%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.03%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.03%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.04%
┃┃┃┃┃┃┃┃┏Current depth: 9        0.04%
┃┃┃┃┃┃┃┏Current depth: 8        0.04%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.05%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.05%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.05%
┃┃┃┃┃┃┃┃┏Current depth: 9        0.06%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.06%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.06%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.07%
┃┃┃┃┃┃┃┃┏Current

┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.71%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.72%
┃┃┃┃┃┃┃┃┏Current depth: 9        0.72%
┃┃┃┃┃┃┃┏Current depth: 8        0.72%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.73%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.73%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.73%
┃┃┃┃┃┃┃┃┏Current depth: 9        0.74%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.74%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.75%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.75%
┃┃┃┃┃┃┃┃┏Current depth: 9        0.75%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.76%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.76%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.76%
┃┃┃┃┃┃┃┃┏Current depth: 9        0.77%
┃┃┃┃┃┃┃┏Current depth: 8        0.77%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.77%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.78%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.78%
┃┃┃┃┃┃┃┃┏Current depth: 9        0.78%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.79%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.79%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        0.79%
┃┃┃┃┃┃┃┃┏Current depth: 9       

┃┃┃┃┃┃┃┃┃┏Current depth: 10        1.42%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        1.42%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        1.42%
┃┃┃┃┃┃┃┃┏Current depth: 9        1.43%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        1.43%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        1.43%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        1.44%
┃┃┃┃┃┃┃┃┏Current depth: 9        1.44%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        1.44%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        1.45%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        1.45%
┃┃┃┃┃┃┃┃┏Current depth: 9        1.45%
┃┃┃┃┃┃┃┏Current depth: 8        1.46%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        1.46%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        1.46%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        1.47%
┃┃┃┃┃┃┃┃┏Current depth: 9        1.47%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        1.47%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        1.48%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        1.48%
┃┃┃┃┃┃┃┃┏Current depth: 9        1.48%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        1.49%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        1.49%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        1.49%
┃┃┃┃┃┃┃┃┏Current depth: 9    

┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.12%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.12%
┃┃┃┃┃┃┃┃┏Current depth: 9        2.12%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.13%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.13%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.13%
┃┃┃┃┃┃┃┃┏Current depth: 9        2.14%
┃┃┃┃┃┃┃┏Current depth: 8        2.14%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.14%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.15%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.15%
┃┃┃┃┃┃┃┃┏Current depth: 9        2.15%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.16%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.16%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.16%
┃┃┃┃┃┃┃┃┏Current depth: 9        2.17%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.17%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.17%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.18%
┃┃┃┃┃┃┃┃┏Current depth: 9        2.18%
┃┃┃┃┃┃┃┏Current depth: 8        2.18%
┃┃┃┃┃┃┏Current depth: 7        2.19%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.19%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.19%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2

┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.84%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.85%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.85%
┃┃┃┃┃┃┃┃┏Current depth: 9        2.85%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.86%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.86%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.86%
┃┃┃┃┃┃┃┃┏Current depth: 9        2.87%
┃┃┃┃┃┃┃┏Current depth: 8        2.87%
┃┃┃┃┃┃┏Current depth: 7        2.87%
┃┃┃┃┃┏Current depth: 6        2.88%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.88%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.88%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.89%
┃┃┃┃┃┃┃┃┏Current depth: 9        2.89%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.89%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.90%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.90%
┃┃┃┃┃┃┃┃┏Current depth: 9        2.90%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.91%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.91%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.91%
┃┃┃┃┃┃┃┃┏Current depth: 9        2.92%
┃┃┃┃┃┃┃┏Current depth: 8        2.92%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        2.92%


...

┃┃┃┃┃┃┃┃┃┏Current depth: 10        97.29%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        97.29%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        97.30%
┃┃┃┃┃┃┃┃┏Current depth: 9        97.30%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        97.30%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        97.31%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        97.31%
┃┃┃┃┃┃┃┃┏Current depth: 9        97.31%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        97.32%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        97.32%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        97.32%
┃┃┃┃┃┃┃┃┏Current depth: 9        97.33%
┃┃┃┃┃┃┃┏Current depth: 8        97.33%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        97.33%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        97.34%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        97.34%
┃┃┃┃┃┃┃┃┏Current depth: 9        97.34%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        97.35%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        97.35%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        97.35%
┃┃┃┃┃┃┃┃┏Current depth: 9        97.36%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        97.36%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        97.36%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        97.37%
┃┃┃┃┃

┃┃┃┃┃┃┃┃┃┏Current depth: 10        97.99%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        97.99%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        98.00%
┃┃┃┃┃┃┃┃┏Current depth: 9        98.00%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        98.01%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        98.01%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        98.01%
┃┃┃┃┃┃┃┃┏Current depth: 9        98.02%
┃┃┃┃┃┃┃┏Current depth: 8        98.02%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        98.02%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        98.03%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        98.03%
┃┃┃┃┃┃┃┃┏Current depth: 9        98.03%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        98.04%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        98.04%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        98.04%
┃┃┃┃┃┃┃┃┏Current depth: 9        98.05%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        98.05%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        98.05%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        98.06%
┃┃┃┃┃┃┃┃┏Current depth: 9        98.06%
┃┃┃┃┃┃┃┏Current depth: 8        98.06%
┃┃┃┃┃┃┏Current depth: 7        98.07%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        98.07%
┃┃┃┃┃┃┃┃┃┏Cu

┃┃┃┃┃┃┃┃┃┏Current depth: 10        98.72%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        98.72%
┃┃┃┃┃┃┃┃┏Current depth: 9        98.73%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        98.73%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        98.73%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        98.74%
┃┃┃┃┃┃┃┃┏Current depth: 9        98.74%
┃┃┃┃┃┃┃┏Current depth: 8        98.74%
┃┃┃┃┃┃┏Current depth: 7        98.75%
┃┃┃┃┃┏Current depth: 6        98.75%
┃┃┃┃┏Current depth: 5        98.75%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        98.76%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        98.76%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        98.76%
┃┃┃┃┃┃┃┃┏Current depth: 9        98.77%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        98.77%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        98.77%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        98.78%
┃┃┃┃┃┃┃┃┏Current depth: 9        98.78%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        98.78%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        98.79%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        98.79%
┃┃┃┃┃┃┃┃┏Current depth: 9        98.79%
┃┃┃┃┃┃┃┏Current depth: 8        98.80%
┃┃┃┃┃┃┃┃┃┏Current depth

┃┃┃┃┃┃┃┃┃┏Current depth: 10        99.41%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        99.41%
┃┃┃┃┃┃┃┃┏Current depth: 9        99.41%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        99.42%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        99.42%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        99.42%
┃┃┃┃┃┃┃┃┏Current depth: 9        99.43%
┃┃┃┃┃┃┃┏Current depth: 8        99.43%
┃┃┃┃┃┃┏Current depth: 7        99.43%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        99.44%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        99.44%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        99.44%
┃┃┃┃┃┃┃┃┏Current depth: 9        99.45%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        99.45%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        99.45%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        99.46%
┃┃┃┃┃┃┃┃┏Current depth: 9        99.46%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        99.46%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        99.47%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        99.47%
┃┃┃┃┃┃┃┃┏Current depth: 9        99.48%
┃┃┃┃┃┃┃┏Current depth: 8        99.48%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        99.48%
┃┃┃┃┃┃┃┃┃┏Current depth: 10        99.49%
┃┃┃┃┃┃┃┃┃┏Cu

FileNotFoundError: [Errno 2] No such file or directory: './tree_data_structure/tree.pkl'

In [13]:
o_tree = open('tree.pkl', 'wb')
pickle.dump(dtmodel_realdata, o_tree)
o_tree.close()

In [30]:
import klepto
d = klepto.archives.dir_archive('stuff.pkl', cached=True, serialized=True)
import numpy
# add three entries to the memory cache
d['big1'] = numpy.arange(1000)
d['big2'] = numpy.arange(1000)
d['big3'] = numpy.arange(1000)
# dump from memory cache to the on-disk archive
d.dump()
# clear the memory cache
d.clear()
d

dir_archive('stuff.pkl', {}, cached=True)